### Checking for availability of GPUs

In [ ]:
!nvidia-smi

### Installing the necessary libraries
Please note that this installation step might fail if no GPU is available.

In [ ]:
!pip install --upgrade pip
!pip install -q -U bitsandbytes
!pip install -q -U git+https://github.com/huggingface/transformers.git
!pip install -q -U git+https://github.com/huggingface/peft.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install -q trl xformers wandb datasets einops gradio sentencepiece
!pip install flash-attn

In [ ]:
# Libraries used for analyzing the dataset
!pip install matplotlib
!pip install statistics

### Importing the necessary libraries and preparation
Here, we set the repos of the base model (to be fine-tuned), the dataset (on which the base model will be fine-tuned) and the output model (the base model fine-tuned on our custom dataset).

In [ ]:
from transformers import (
    AutoModelForCausalLM, 
    AutoTokenizer, 
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline, 
    logging, 
    TextStreamer,
    GenerationConfig
)
from peft import (
    LoraConfig, 
    PeftModel, 
    prepare_model_for_kbit_training, 
    get_peft_model
)
import os
import torch
import wandb
import platform
import warnings
from datasets import load_dataset
from trl import SFTTrainer
from huggingface_hub import notebook_login

# Base model
base_model = "mistralai/Mistral-Nemo-Instruct-2407"

# Custom dataset and new model to be created
dataset_name = "dataset/repo"

# New model to be created
new_model = "model/repo"

# Ignore all warnings
warnings.filterwarnings("ignore")

### Logging into Hugging Face
Since both our dataset and the model we want to create are (meant to be) private, it is better to already log into our HF account.

In [ ]:
# We already log into our own hugging face hub with a 'WRITE' token
!huggingface-cli login --token MY_HF_WRITE_TOKEN

*Remark:* an alternative is to simply write
```
notebook_login()
```
and then type the HF 'WRITE' token.

### Loading the dataset

Our dataset here is of the form:

```json
   [
       {
           "source": "Chat no 1-1",
           "text": [
               {"role": "user", "content": "My system prompt\n\nQuestion 11"},
               {"role": "assistant", "content": "Answer 11"}
           ]
       },
       {
           "source": "Chat no 1-2",
           "text": [
               {"role": "user", "content": "Question 11"},
               {"role": "assistant", "content": "Answer 11"},
               {"role": "user", "content": "My system prompt\n\nQuestion 12"},
               {"role": "assistant", "content": "Answer 12"}
           ]
       },
       {
           "source": "Chat no 2",
           "text": [
               {"role": "user", "content": "My system prompt\n\nQuestion 21"},
               {"role": "assistant", "content": "Answer 21"}
   ]
```

We will convert it later on using the chat template that comes with the tokenizer.

*Remark:* Note that the system prompt is included in the very last user message of each "chats" that make up the dataset. This is because, even though Nemo supports system prompts (as per the Jinja code given after executing ```tokenizer.chat_template```), there seem to be an issue with the tokenizer in this respect. It will produce the same effect anyway (the model is supposed to be aware with this way of doing).

In [ ]:
# Loading the dataset
dataset = load_dataset(dataset_name, split="train", encoding='latin-1')

# We "shuffle" the dataset
dataset = dataset.shuffle()

dataset["text"][0]

### Loading the base model

In [ ]:
# The quantization to apply to the base model
bnb_config = BitsAndBytesConfig(
    load_in_4bit= True,
    bnb_4bit_quant_type= "nf4",
    bnb_4bit_compute_dtype= torch.bfloat16,
    bnb_4bit_use_double_quant= False,
)

# We load quantized base model
model = AutoModelForCausalLM.from_pretrained(
    base_model,
    quantization_config=bnb_config,
    device_map="auto",
    attn_implementation="flash_attention_2"
)

model.config.use_cache = False
model.config.pretraining_tp = 1
model.gradient_checkpointing_enable()

### Loading the tokenizer

In [ ]:
# Load tokenizer
tokenizer = AutoTokenizer.from_pretrained(base_model, trust_remote_code=True)
tokenizer.padding_side = 'right'

To avoid breaking French punctuation rules, we have to make sure that the following defaults as ```False```.

In [ ]:
tokenizer.clean_up_tokenization_spaces

We now have to set the PAD token. But, first of all, we need to check whether the tokenizer already has one.

In [ ]:
print(tokenizer.pad_token)

If not, then we have to set it:

In [ ]:
tokenizer.pad_token = tokenizer.unk_token

*Remark:* The value set for the PAD token might differ from a model to another. Sometimes ```<pad>``` or ```[pad]``` might be a better choice. The best way for choosing the right value is to check the tokenizer's vocabulary.

Let's check that it worked:

In [ ]:
print(tokenizer.pad_token)

Now, let's add the PAD and EOS tokens to the tokenizer:

In [ ]:
tokenizer.add_pad_token = True
tokenizer.add_eos_token = True

### Formatting the dataset
Having loaded and configured the tokenizer, we can now apply the appropriate chat template to our dataset, namely:
```
<s>[INST] My first question. [/INST]The model's answer to my question.</s> [INST] A follow-up question. [/INST]The model's answer to my follow-up question.</s>
```
Note that, to avoid having extra/undesired "Assistant:" or "User:" tags placed at the end of each instances of the dataset, it is necessary to specify ```add_generation_prompt=False``` when applying the chat template.

In [ ]:
from datasets import Dataset
import json

# Creating a list with elements of the dataset properly formatted
formatted_dataset = [tokenizer.apply_chat_template(conv, tokenize=False, add_generation_prompt=False)[3:] for conv in dataset["text"]]

# Converted dataset with appropriate chat template
ds = Dataset.from_dict({"text": formatted_dataset})

In [ ]:
# Let's have a look
print(ds["text"][100])

*Remark:* We added ```[3:]``` to elements of ```formatted_dataset``` in order to remove the very first ```<s>``` (BOS) token because the tokenizer adds it automatically. Otherwise we would have two BOS at the beginning, which might bring some trouble. To double check it suffices to decode the encoded data:

In [ ]:
print(tokenizer.decode(tokenizer.encode(ds["text"][35])))

The very first BOS and the very last EOS have indeed been added by the tokenizer, matching the chat template!

### Rapid analysis of the tokenized dataset
Unfortunately, LLMs have limited (yet modulable) context windows, so it is worth analyzing our dataset in order to know which context length better fits our needs. Indeed, later on we will need to specify the length of the inputs used for fine-tuning (i.e. to set ```max_seq_length``` in the ```SFTTrainer()```). 

Concretely, we will have a look at the distribution of the length of each tokenized example. We will first (i) compute the list of all such tokenized examples and then (ii) plot it to analyze it more conveniently.

In [ ]:
# We compute the list of all the lengths of the tokenized examples
length_examples = []
for i in range(len(ds)):
    size = len(tokenizer.encode(ds["text"][i]))
    length_examples.append(size)

In [ ]:
import matplotlib.pyplot as plt
from collections import Counter

# We count the occurrences of each integer
counter = Counter(length_examples)

# We get the integers and their corresponding counts
x = list(counter.keys())
y = list(counter.values())

# We sort the integers (x-axis)
x_sorted, y_sorted = zip(*sorted(zip(x, y)))

# We plot the values
plt.bar(x_sorted, y_sorted)
plt.xlabel('Number of tokens')
plt.ylabel('Number of Occurrences')
plt.title('Distribution of lengths of tokenized dataset examples')
plt.show()

To understand more precisely the dataset, we can calculate, say, the $90$th percentile value of the lengths of our tokenized examples. Roughly speaking, this means determining, for any $p\in(0,1)$, the smallest integer $N=N(p)\in\mathbb{N}$ such that
<p style="text-align: center;">$F_X(N)=\mathbb{P}(X\leq N)=p,$</p>
where $F_X$ is the cumulative distribution function of the tokenized dataset and $X$ the length of a random example.

In [ ]:
from statistics import mean
import numpy as np

# Target percentile
p = 0.9

def find_percentile_value(arr,percentile):
    if not arr:
        raise ValueError("The list should not be empty")
    arr.sort()  # Sort the list
    # Calculate the index for the pth percentile
    index = int(percentile * len(arr)) - 1
    # Handle edge cases where index might be out of bounds
    index = max(0, min(index, len(arr) - 1))
    return arr[index]

percentile_value = find_percentile_value(length_examples,p)
print("The minimum value is:", min(length_examples))
print("The arithmetic mean is:", int(np.floor(mean(length_examples))))
print("The "+str(int(p*100))+"th percentile value is:", percentile_value)
print("The maximum value is:", max(length_examples))

### Data collation

We now need to pass the dataset through a data collator. The point here is to "mask" the "user questions" (prompts) within the dataset, so that the model learns the "answers" only (there is no point in learning the questions, they should only serve as context). 

What the collator does is that it will use the instruction/response templates to locate the starts of user input and starts of assistant response. It then fill those sections with $-100$ tokens, which will be ignored during training (that’s how the user inputs are masked to prevent them from contributing to the loss).

In [ ]:
from transformers import DataCollatorForLanguageModeling
import torch

class CustomDataCollator(DataCollatorForLanguageModeling):
    def __init__(self, tokenizer, mlm=False):
        super().__init__(tokenizer=tokenizer, mlm=mlm)
        self.inst_token = tokenizer.encode('[INST]', add_special_tokens=False)[0]
        self.inst_end_token = tokenizer.encode('[/INST]', add_special_tokens=False)[0]
        self.eos_token = tokenizer.eos_token_id

    def torch_call(self, examples):
        batch = super().torch_call(examples)

        for i, input_ids in enumerate(batch['input_ids']):
            # Find positions of [INST], [/INST], and EOS tokens
            inst_positions = torch.where(input_ids == self.inst_token)[0]
            inst_end_positions = torch.where(input_ids == self.inst_end_token)[0]
            eos_positions = torch.where(input_ids == self.eos_token)[0]

            if len(inst_positions) > 0 and len(eos_positions) > 0:
                # Find the start of the last assistant response
                last_inst_end_pos = inst_end_positions[-1]
                
                # Mask everything before the last assistant response
                batch['labels'][i, :last_inst_end_pos+1] = -100

                # If there's an EOS token after the last [/INST], unmask until that EOS
                if eos_positions[-1] > last_inst_end_pos:
                    batch['labels'][i, last_inst_end_pos+1:eos_positions[-1]+1] = input_ids[last_inst_end_pos+1:eos_positions[-1]+1]
                else:
                    # If no EOS after last [/INST], unmask until the end
                    batch['labels'][i, last_inst_end_pos+1:] = input_ids[last_inst_end_pos+1:]

        return batch

# We now define the collator
collator = CustomDataCollator(tokenizer=tokenizer)

Let's check that the data collator has appropriately handled the question/answer turns:

In [ ]:
# We apply the collator to a sample of the dataset
collated_data = collator([tokenizer(ds["text"][1])])['labels'][0]

# We convert the above to a list (so as to be able to print everything)
collated_data_list = collated_data.tolist()
print(collated_data_list)

*Remark:* The only thing that should not be masked as "$-100$" tokens in the very last "assistant" message.

### Setting LoRA parameters and modules

Here, we will do two things: setting the LoRA parameters $r$ and $\alpha$, and setting the target modules to be trained.

##### LoRA parameters
The values $\alpha=r$ or $\alpha=2r$ (considered a "sweet spot"), with $r$ a power of $2$, are conventional (see LoRA paper in the link below). The latter is often used to have more emphasis and the new data. 
(See: https://arxiv.org/pdf/2106.09685)

##### LoRA modules
The LoRA modules are, essentially, the matrices that the model allows us to train. Their name may depend on the model, which is why it is recommended to look at what it looks like via the command:

In [ ]:
print(model)

(Look for linear modules.) 
In most cases (Mistral, Llama, etc), however, the modules are something like:
```
["q_proj", "k_proj", "v_proj", "o_proj", "gate_proj", "up_proj", "down_proj", "lm_head"]
```
but they sometimes bear different names (e.g. with Falcon models).

In [ ]:
# Adding the adapters in the layers
model = prepare_model_for_kbit_training(model)

# LoRA config
peft_config = LoraConfig(
        r=256,
        lora_alpha=256,
        lora_dropout=0.05, # Conventional
        bias="none",
        task_type="CAUSAL_LM",
        target_modules="all-linear"
    )

# We add the LoRA "adapters" to the model
model = get_peft_model(model, peft_config)

*Remark:* In most cases, one can simply set:
```
target_modules = 'all-linear'
```
but this might raise an error for some models (e.g. with Google's Gemma-2B).

(See: https://stackoverflow.com/questions/76768226/target-modules-for-applying-peft-lora-on-different-models)

### Setting Weights & Biases for monitoring purposes

This will allow us to monitor the training directly from W&B.

In [ ]:
# Monitering the LLM from WandB
wandb.login(key = "MY_WANDB_KEY")
run = wandb.init(project='MyProjectName', job_type="training", anonymous="allow")

### Setting training parameters
Here, we set the hyperparameters (epochs, batch, etc.) as well as the SFT (i.e. Supervised Fine-Tuning) parameters.

In [ ]:
# Hyperparamter
training_arguments = TrainingArguments(
    output_dir= "./results",
    num_train_epochs= 3,              # total number of training epochs
    per_device_train_batch_size= 4,   # batch size per device during training (the higher the better)
    gradient_accumulation_steps= 8,
    optim = "paged_adamw_8bit",
    save_steps= 1000,                 # Save checkpoints #every 50 steps
    logging_steps= 15,                # When to start reporting loss
    learning_rate= 2e-5,              # We take a not too small value given that new tokens have been added
    weight_decay= 0.001,              # strength of weight decay
    fp16= False,
    bf16= False,
    max_grad_norm= 0.3,
    max_steps= -1,
    warmup_ratio= 0.3,                # number of warmup steps for learning rate scheduler
    group_by_length= True,            # Group sequences into batches with same length (saves memory and speeds up training considerably)
    lr_scheduler_type="constant",
    report_to="wandb",
)

# Setting SFT parameters
trainer = SFTTrainer(
    model=model,                         # the instantiated HF Transformers model to be trained
    train_dataset=ds,                    # Training dataset
    data_collator=collator,              # Making sure that data collator correction is taken into account
    peft_config=peft_config,
    max_seq_length=4096,
    dataset_text_field="text",           # Column of the dataset to be used for training
    tokenizer=tokenizer,
    args=training_arguments,             # training arguments, defined above
    packing= False,
)

### Training and saving the model
A progression bar will soon appear displaying a number of steps which corresponds to
<p style="text-align: center;">$ \#\verb"steps" = \left\lceil\displaystyle\frac{\verb"total_dataset_size"\times\#\verb"epochs"}{\verb"batch_size"}\right\rceil, $</p>
where
<p style="text-align: center;">$\verb"batch_size" = \verb"per_device_train_batch_size" \times \verb"gradient_accumulation_steps",$</p>

and $\left\lceil\cdot\right\rceil$ is the ceiling function.

In [ ]:
# Training the model
trainer.train()

# Save the fine-tuned model
trainer.model.save_pretrained(new_model)
wandb.finish()
model.config.use_cache = True
model.eval()

#######################################################
# We save the model in the same cell, to avoid weird  #
#    behaviors induced by GPU providers (Colab...)    #
#######################################################

# Clear the memory footprint (NB: pretrained model has been saved to "new_model")
del model, trainer
torch.cuda.empty_cache()
print("Memory footprint has been cleared.")

# Reload the base model
base_model_reload = AutoModelForCausalLM.from_pretrained(
    base_model, low_cpu_mem_usage=True,
    return_dict=True,torch_dtype=torch.bfloat16,
    device_map= "auto")
print("Base model has been reloaded.")

# Merging the adapter with model
model = PeftModel.from_pretrained(base_model_reload, new_model)
model = model.merge_and_unload()
print("Adapter has been merged to the base model.")

# Reload tokenizer
tokenizer = AutoTokenizer.from_pretrained(base_model, trust_remote_code=True)
tokenizer.padding_side = "right"
tokenizer.pad_token = tokenizer.unk_token
tokenizer.add_pad_token = True
print("Tokenizer has been reloaded.")

# Pushing the merged model to hugging face hub
model.push_to_hub(repo_id='New_model_name', private=True)
tokenizer.push_to_hub(repo_id='New_model_name', private=True)

Et voilà !…